In [5]:
import numpy as np
import random
import pandas as pd
import os

from common import OUTPUTPATH
from models import linear_pcc
import data

In [6]:
# estimators here
linear_pcc.fit(data.x1, data.y)

In [3]:
num_importance = 100 # defult values show all variables
from sklearn.inspection import permutation_importance

def individual_importance_dataframe(est, X, y, scoring='neg_log_loss', num_importance=100000, n_repeats=100, seeds=None):
    """
    This algorithm use linear estimators and get the importance variables where p < 0.05
    To easy comparison, we set importance score: 1- p
    """
    r = permutation_importance(est, X, y, n_repeats=n_repeats, scoring=scoring, random_state=seeds)
    non_zero_indx = np.where(r.importances_mean > 0)
    indx = r.importances_mean[non_zero_indx].argsort()[::-1]
    important_variables = X.columns[non_zero_indx][indx]
    importance_scores = r.importances_mean[non_zero_indx][indx]
    coef = est.coef_[0][non_zero_indx][indx]
    df = pd.DataFrame({'variables': important_variables[:num_importance], 'coef': coef[:num_importance], 'importance': importance_scores[:num_importance]})
    return df

def linear_importance_dataframe(est, X, y, scoring = 'neg_log_loss', num_importance=100000, n_repeats=100, seeds=None):
    """
    Combine all morphologies plots together
    """
    data1 = pd.concat([X, y], axis=1)
    cnt = None
    for i in range(3):
        col_indx = -4 + i

        estimator, X, y = est[i], data1.iloc[:, :col_indx], data.y.iloc[:, i]
        temp_df = individual_importance_dataframe(est=estimator, X=X, y=y, scoring=scoring, num_importance=num_importance, n_repeats=n_repeats, seeds=seeds)
        if not cnt: 
            df = temp_df
            cnt = 1
        else:
            df = pd.concat([df, temp_df], axis=1)

    upper_columns = ['Sphere', 'Worm', 'Vesicle']
    lower_columns = ['variables', 'coef', 'importance']
    df.columns = pd.MultiIndex.from_product([upper_columns, lower_columns], names=['Phase', 'Property'])
    return df

show all importance dataframe for Sphere, Worm, Vesicle

In [9]:
linear_importance_dataframe(linear_pcc.fitted_, data.abbrev_x1, data.y, num_importance=100000, seeds=1000, n_repeats=500)

/usr/local/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/usr/local/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/usr/local/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/usr/local/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/usr/local/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/usr/local/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  w

Phase         Sphere                                Worm            \
Property   variables      coef    importance   variables      coef   
0         mw_tot_cre  0.000781  8.263130e+00  mw_tot_cre -0.000436   
1         mv_tot_cre -0.050703  4.039665e+00  mv_tot_cre  0.025036   
2             dp_cre -0.056522  3.826610e+00      dp_cre  0.027473   
3           apol_cna  0.257623  1.199842e+00  mw_tot_cna -0.000258   
4            psa_cna -0.037091  2.475773e-01    apol_cna -0.062277   
5             dp_cna  0.049359  2.380387e-01  mv_tot_cna  0.024094   
6         mv_tot_cna  0.040055  1.922278e-01        conc  0.072983   
7            psa_cre -0.206010  1.491745e-01      mw_cna  0.005097   
8               conc -0.127560  7.881694e-02     psa_cre  0.055504   
9         mw_tot_cna -0.000103  2.148267e-02     psa_cna  0.007698   
10            mw_cre  0.028013  1.600846e-02      mw_cre -0.024466   
11            mw_cna -0.003501  1.330534e-02        temp  0.019550   
12         clogp_cna  0.020923  9.176250e-04      dp_cna  0.004539   
13          apol_cre  0.019163  9.146186e-04      sphere -0.016023   
14              temp -0.011317  8.677913e-04   clogp_cna -0.008845   
15           charged  0.021135  2.763879e-04    apol_cre  0.002626   
16                ph -0.020380  1.017749e-04     charged -0.005067   
17        mass_ratio  0.008822  4.521703e-05   clogp_cre -0.004384   
18         vol_ratio  0.008712  4.446727e-05  mass_ratio -0.001474   
19         clogp_cre  0.011543  4.155282e-05   vol_ratio -0.001363   
20            mv_cre  0.000570  8.912255e-07      mv_cna  0.000923   
21               NaN       NaN           NaN        salt -0.000361   
22               NaN       NaN           NaN      mv_cre  0.000133   
23               NaN       NaN           NaN         NaN       NaN   
24               NaN       NaN           NaN         NaN       NaN   

Phase                      Vesicle                          
Property    importance   variables      coef    importance  
0         6.320292e+00  mw_tot_cre -0.000936  7.715791e+00  
1         1.631529e+00  mv_tot_cre  0.080782  7.336668e+00  
2         1.490471e+00      dp_cre  0.041079  3.312259e+00  
3         1.590352e-01  mw_tot_cna -0.000785  1.013335e+00  
4         1.376481e-01  mv_tot_cna  0.080923  5.745564e-01  
5         7.833423e-02    apol_cna -0.128724  3.902514e-01  
6         4.419836e-02     psa_cna  0.039046  3.075598e-01  
7         3.448851e-02      sphere -0.697121  5.157315e-02  
8         2.518712e-02   clogp_cna -0.194776  3.248889e-02  
9         1.870047e-02     psa_cre  0.086631  2.700510e-02  
10        7.314210e-03        conc  0.056344  2.258747e-02  
11        7.108344e-03      mw_cre -0.036125  1.508148e-02  
12        2.969675e-03          ph -0.142967  1.197600e-02  
13        8.021883e-04        temp  0.029290  1.142383e-02  
14        2.647471e-04        worm -0.248615  9.166179e-03  
15        1.026467e-04    apol_cre  0.042498  2.866938e-03  
16        9.464587e-05     charged -0.141321  1.481643e-03  
17        4.627542e-05  mass_ratio -0.104957  1.067505e-03  
18        6.785273e-06   vol_ratio -0.101589  1.002529e-03  
19        5.849809e-06      dp_cna -0.002743  6.948553e-04  
20        2.560544e-06      mw_cna -0.000616  2.685763e-04  
21        4.122352e-07      mv_cna  0.015011  6.266795e-05  
22        2.450126e-07   clogp_cre -0.023424  2.409437e-05  
23                 NaN        salt -0.004210  2.118180e-06  
24                 NaN      mv_cre  0.000180  2.597478e-07

In [5]:
top5_linear_dataframe = linear_importance_dataframe(linear_pcc.fitted_, data.abbrev_x1, data.y, num_importance=5, seeds=1000)
top5_linear_dataframe.to_csv(os.path.join(OUTPUTPATH, 'Top5_linear_dataframe.csv'))
top5_linear_dataframe

/Users/yluu0028/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/Users/yluu0028/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/Users/yluu0028/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/Users/yluu0028/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/Users/yluu0028/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but LogisticRegressionCV was fitted without feature names
  warnings.warn(
/Users/yluu0028/opt/anaconda3/lib/python3.9/site-packages/sk

Phase         Sphere                             Worm                       \
Property   variables      coef importance   variables      coef importance   
0         mw_tot_cre  0.000781   8.209574  mw_tot_cre -0.000436   6.328502   
1         mv_tot_cre -0.050703   4.059840  mv_tot_cre  0.025036   1.611345   
2             dp_cre -0.056522   3.846369      dp_cre  0.027473   1.473559   
3           apol_cna  0.257623   1.206764  mw_tot_cna -0.000258   0.157105   
4            psa_cna -0.037091   0.248166    apol_cna -0.062277   0.137773   

Phase        Vesicle                       
Property   variables      coef importance  
0         mw_tot_cre -0.000936   7.671937  
1         mv_tot_cre  0.080782   7.356431  
2             dp_cre  0.041079   3.334120  
3         mw_tot_cna -0.000785   1.012136  
4         mv_tot_cna  0.080923   0.577537